# IMPORT LIBRARY

In [116]:
!pip install emoji
!pip install emoticon_fix

In [117]:
import numpy as np
import pandas as pd
import gensim
import re
import nltk
import string
import emoji
from emoticon_fix import emoticon_fix
from bs4 import BeautifulSoup
from nltk import pos_tag
from nltk import ne_chunk
from nltk.tree import Tree
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from gensim.models import Word2Vec
from nltk.tokenize import word_tokenize
from sklearn.metrics.pairwise import cosine_similarity

In [118]:
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [119]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [120]:
nltk.download('maxent_ne_chunker')

[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!


True

In [121]:
nltk.download('words')

[nltk_data] Downloading package words to /root/nltk_data...
[nltk_data]   Package words is already up-to-date!


True

In [139]:
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/MyDrive/bangkit_recommender

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/MyDrive/bangkit_recommender


In [141]:
data = pd.read_csv("vegan_recipes.csv")

In [142]:
data.head()

href                  title  \
0        https://veganuary.com/recipes/rainbow-rice/           Rainbow Rice   
1          https://veganuary.com/recipes/mfc-nachos/                 Nachos   
2   https://veganuary.com/recipes/hazelnut-truffles/      Hazelnut Truffles   
3  https://veganuary.com/recipes/simple-roasted-r...  Simple Roasted Radish   
4  https://veganuary.com/recipes/baked-apple-char...  Baked Apple Charlotte   

                                         ingredients  \
0  \nIngredients\n\nCarrot ribbons (just use a pe...   
1  \nIngredients\n\n400g Meatless Farm Co mince (...   
2  \nIngredients\n\n100g hazelnuts\n2 tablespoons...   
3  \nIngredients\n\n1 170g tub beetroot and horse...   
4  \nIngredients\n\n2 tbsp rapeseed oil\n75g pitt...   

                                         preparation calories carb protein  \
0  \nMethod\n\nCook the rice as instructed on the...      450   64      10   
1  \nPreparation\n\nPreheat the oven to 350ºF\nHe...      483   42      20   
2  \nMethod\n\nPreheat the oven to 200c\nPut the ...      146    7       1   
3  \nPreparation\nPre heat the oven to 160°C\nCut...       96    7       1   
4  \nPreparation\n\nServes 9\nYou will need an 8i...      415   51       3   

    fat        types category  is_diary  \
0    19  main course   dinner         0   
1    27       snacks   dinner         1   
2  12,2      dessert   dinner         0   
3     7  main course   dinner         0   
4    22  main course   dinner         1   

                                            img_link  
0  https://veganuary.com/wp-content/uploads/2016/...  
1  https://veganuary.com/wp-content/uploads/2018/...  
2  https://veganuary.com/wp-content/uploads/2016/...  
3  https://veganuary.com/wp-content/uploads/2019/...  
4  https://veganuary.com/wp-content/uploads/2016/...

In [143]:
len(data.preparation[3])

311

In [144]:
data.preparation[3]

'\nPreparation\nPre heat the oven to 160°C\nCut the radishes in half and place in a baking dish, drizzle with the oil and roast for about 20minutes.\nSpread the houmous onto a serving plate.\nRemove from the oven and season with salt.\nSpoon on top of the beetroot and horseradish houmous\n\xa0\nCredit: @natalie.naturally\n'

In [145]:
len(data.ingredients[3])

108

In [146]:
data.ingredients[3]

'\nIngredients\n\n1 170g tub beetroot and horseradish houmous\n300g mixed radishes\n2 tbsp. light oil\n1 tsp salt\n\n'

# PREPROCESSING

In [147]:
def filter_rows(row):
    # Check for image or web links and length
    if ("<img" in row["preparation"]) or ("http" in row["preparation"]) or ("image" in row["preparation"]) or (len(row["preparation"]) <= 400) or (len(row["ingredients"]) <= 200):
        return False
    return True

# Apply the filter function to the DataFrame
data = data[data.apply(filter_rows, axis=1)].reset_index(drop=True)

In [148]:
def preparation_prepro(text):
    # Replace "Method" or "Preparation" with "Instruction :"
    text = re.sub('Method', '', text, flags=re.IGNORECASE)
    text = re.sub('Instructions', 'Instruction :', text, flags=re.IGNORECASE)
    text = re.sub('Preparation', 'Instruction :', text, flags=re.IGNORECASE)

    # Remove lines containing "Serves" and similar patterns
    text = re.sub(r'\bServes\b[^\n]*\n', '', text)
    text = re.sub(r'\bServings?\b[^\n]*\n', '', text)
    text = re.sub(r'\bPortions?\b[^\n]*\n', '', text)

    # Remove extra line breaks
    text = re.sub(r'\n+', '\n', text)

    # Remove leading and trailing whitespaces
    text = text.strip()


    return text

# Apply the function to the "preparation" column
data["preparation"] = data["preparation"].apply(preparation_prepro)



In [149]:
def ingredients_prepro(text):
    # Remove special characters and multiple spaces
    text = re.sub(r'[^A-Za-z0-9\s\n]', '', text)

    # Remove bullet points and numbers
    text = re.sub(r'[\u2022\u2023\u2024\u2027\u25CF\u25E6\u25A0\u25AA\u25A1*]\s?\d*\s?', '', text)

    # Convert specific units to more standard units (customize as needed)
    text = re.sub(r'ml', 'cups', text)
    text = re.sub(r'tsp', 'tsp', text)
    text = re.sub(r'tbsp', 'tbsp', text)
    text = re.sub('Ingredients', 'Ingredients :', text)

    return text



data["ingredients"] = data["ingredients"].apply(ingredients_prepro)

In [150]:
data['title'].duplicated().sum()

13

In [151]:
data.loc[data['title'].duplicated()]

href  \
193   https://veganuary.com/recipes/meatless-farm-ve...   
228        https://veganuary.com/recipes/tofu-scramble/   
399    https://veganuary.com/recipes/vegetable-curry-2/   
400     https://veganuary.com/recipes/chilli-non-carne/   
428        https://veganuary.com/recipes/carrot-cake-2/   
485     https://veganuary.com/recipes/chocolate-cake-2/   
754   https://simple-veganista.com/raw-creamy-miso-s...   
782   https://simple-veganista.com/savory-chickpea-p...   
837   https://simple-veganista.com/orange-french-toa...   
1010         https://simple-veganista.com/raw-pad-thai/   
1023   https://simple-veganista.com/salsa-verde-recipe/   
1091     https://simple-veganista.com/stuffed-avocados/   
1113  https://simple-veganista.com/vegan-peanut-butt...   

                                    title  \
193                  Vegan Butter Chicken   
228                         Tofu Scramble   
399                       Vegetable Curry   
400                      Chilli Non Carne   
428                           Carrot Cake   
485                        Chocolate Cake   
754   RAW CREAMY MISO SOUP WITH MUSHROOMS   
782          SAVORY CHICKPEA PANCAKE (GF)   
837           ORANGE FRENCH TOAST (VEGAN)   
1010                         RAW PAD THAI   
1023                TOMATILLO SALSA VERDE   
1091                     Stuffed Avocados   
1113          VEGAN PEANUT BUTTER COOKIES   

                                            ingredients  \
193   \nIngredients :\n4 Meatless Farm Chicken Breas...   
228   \nIngredients :\n\n1 tablespoon toasted sesame...   
399   \nIngredients :\n\n70g raw cashews\nOptional 1...   
400   \nIngredients :\n\nOlive Oil\n1 x large onion ...   
428   \nIngredients :\n\n1 tablespoon lemon juice\n1...   
485   \nIngredients :\n\n300 g soya spread baking  s...   
754   \n\n\nIngredients :\n\n\n\nScale\n1x2x3x \n\n\...   
782   \n\n\nIngredients :\n\n\n\nScale\n1x2x3x \n\n\...   
837   \n\n\nIngredients :\n\n\n\nScale\n1x2x3x \n\n\...   
1010  \n\n\nIngredients :\n\n\n\nScale\n1x2x3x \n\n\...   
1023  \n\n\nIngredients :\n\n\n\nUnits\nUSM \n\nScal...   
1091  \n\n\nIngredients :\n\n\n\nScale\n1x2x3x \n\n\...   
1113  \n\n\nIngredients :\n\n\n\nUnits\nUSM \n\nScal...   

                                            preparation calories  carb  \
193   1. Pre-heat your oven to 180.C\n2. Melt the bu...      348    69   
228   Heat the oil in a heavy frying pan over a medi...      225     7   
399   In a small bowl, cover the raw cashews with co...      350    25   
400   Instruction :\nThis is a meal that you will ma...      387    25   
428   Preheat oven to 180° C, 160° C fan, Gas mark 4...      265    39   
485   Cake\nPreheat the oven to 185°C.\nBeat the Pro...      300    35   
754   Instruction :\nMushrooms: Start with the mushr...      214    40   
782   Instruction :\nPreheat griddle on medium.\nMix...      151    35   
837   Instruction :\nPreheat a griddle according to ...      365    40   
1010  Instruction :\nSauce: In a small/medium bowl, ...      306  33,2   
1023  Instruction :\nSimmer: In a medium pot, add th...       15   3,3   
1091  Instruction :\nPrepare the ingredients. Once y...      140   9,6   
1113  Instruction :\nPreheat the oven to 350 degrees...      125  15,3   

     protein   fat        types   category  is_diary img_link  
193        4     9  main course     dinner         1      NaN  
228       15    14  main course  breakfast         0      NaN  
399        5    17  main course     dinner         0      NaN  
400       36    17  main course     dinner         0      NaN  
428        3    12      dessert     dinner         1      NaN  
485        5    10      dessert     dinner         1      NaN  
754       20    15  main course     dinner         0      NaN  
782        5    10      dessert  breakfast         0      NaN  
837       20    15  main course  breakfast         1      NaN  
1010    11,1  17,4  main course     dinner         1      NaN  
1023     0,4   0,1  main 

In [152]:
data.drop_duplicates(subset=["title"], inplace=True)

In [153]:
data.loc[data['title'].duplicated()]

Empty DataFrame
Columns: [href, title, ingredients, preparation, calories, carb, protein, fat, types, category, is_diary, img_link]
Index: []

In [154]:
data.to_csv('data_vegan.csv', index=False)

In [155]:
data = pd.read_csv("data_vegan.csv")

In [156]:
df = data.copy()
df.head()

href  \
0        https://veganuary.com/recipes/rainbow-rice/   
1          https://veganuary.com/recipes/mfc-nachos/   
2  https://veganuary.com/recipes/baked-apple-char...   
3  https://veganuary.com/recipes/choc-and-raspber...   
4  https://veganuary.com/recipes/nakd-mini-bakewe...   

                         title  \
0                 Rainbow Rice   
1                       Nachos   
2        Baked Apple Charlotte   
3  Choc and Raspberry Porridge   
4     Nākd Mini Bakewell Tarts   

                                         ingredients  \
0  \nIngredients :\n\nCarrot ribbons just use a p...   
1  \nIngredients :\n\n400g Meatless Farm Co mince...   
2  \nIngredients :\n\n2 tbsp rapeseed oil\n75g pi...   
3  \nIngredients :\n\nPorridge\n50g gluten free r...   
4  \nIngredients :\n\nFor the shortcrust pastry\n...   

                                         preparation calories carb protein  \
0  Cook the rice as instructed on the packaging.\...      450   64      10   
1  Instruction :\nPreheat the oven to 350ºF\nHeat...      483   42      20   
2  Instruction :\nYou will need an 8inch/23cm squ...      415   51       3   
3  Add the gluten free oats, water and your chose...      157   26       5   
4  Instruction :\nInstruction : time: 15 minutes,...      137   18     2,6   

   fat        types category  is_diary  \
0   19  main course   dinner         0   
1   27       snacks   dinner         1   
2   22  main course   dinner         1   
3    5  main course   dinner         1   
4  5,9  main course   dinner         0   

                                            img_link  
0  https://veganuary.com/wp-content/uploads/2016/...  
1  https://veganuary.com/wp-content/uploads/2018/...  
2  https://veganuary.com/wp-content/uploads/2016/...  
3                                                NaN  
4                                                NaN

In [157]:
# Data Info
list_item = []
for col in df.columns:
    list_item.append([col, df[col].dtype, df[col].isna().sum(), 100*df[col].isna().sum()/len(df[col]), df[col].nunique(), df[col].unique()])
desc_data = pd.DataFrame(data=list_item, columns='feature data_type null_num null_pct unique_num unique_sample'.split())
desc_data

feature data_type  null_num   null_pct  unique_num  \
0          href    object         0   0.000000        1111   
1         title    object         0   0.000000        1111   
2   ingredients    object         0   0.000000        1111   
3   preparation    object         0   0.000000        1111   
4      calories    object         0   0.000000         400   
5          carb    object         0   0.000000         304   
6       protein    object         0   0.000000         212   
7           fat    object         0   0.000000         196   
8         types    object         0   0.000000           3   
9      category    object         0   0.000000           3   
10     is_diary     int64         0   0.000000           2   
11     img_link    object      1082  97.389739          29   

                                        unique_sample  
0   [https://veganuary.com/recipes/rainbow-rice/, ...  
1   [Rainbow Rice, Nachos, Baked Apple Charlotte, ...  
2   [\nIngredients :\n\nCarrot ribbons just use a ...  
3   [Cook the rice as instructed on the packaging....  
4   [450, 483, 415, 157, 137, 120, 174,7, 288, 346...  
5   [64, 42, 51, 26, 18, 2, 43,9, 31, 15, 58, 7, 4...  
6   [10, 20, 3, 5, 2,6, 2, 15,9, 15, 17, 6,8, 21,2...  
7   [19, 27, 22, 5, 5,9, 11, 19,4, 12, 20, 7, 6, 2...  
8                      [main course, snacks, dessert]  
9                          [dinner, lunch, breakfast]  
10                                             [0, 1]  
11  [https://veganuary.com/wp-content/uploads/2016...

In [158]:
df = df.drop('href', axis=1)
df.head()

title  \
0                 Rainbow Rice   
1                       Nachos   
2        Baked Apple Charlotte   
3  Choc and Raspberry Porridge   
4     Nākd Mini Bakewell Tarts   

                                         ingredients  \
0  \nIngredients :\n\nCarrot ribbons just use a p...   
1  \nIngredients :\n\n400g Meatless Farm Co mince...   
2  \nIngredients :\n\n2 tbsp rapeseed oil\n75g pi...   
3  \nIngredients :\n\nPorridge\n50g gluten free r...   
4  \nIngredients :\n\nFor the shortcrust pastry\n...   

                                         preparation calories carb protein  \
0  Cook the rice as instructed on the packaging.\...      450   64      10   
1  Instruction :\nPreheat the oven to 350ºF\nHeat...      483   42      20   
2  Instruction :\nYou will need an 8inch/23cm squ...      415   51       3   
3  Add the gluten free oats, water and your chose...      157   26       5   
4  Instruction :\nInstruction : time: 15 minutes,...      137   18     2,6   

   fat        types category  is_diary  \
0   19  main course   dinner         0   
1   27       snacks   dinner         1   
2   22  main course   dinner         1   
3    5  main course   dinner         1   
4  5,9  main course   dinner         0   

                                            img_link  
0  https://veganuary.com/wp-content/uploads/2016/...  
1  https://veganuary.com/wp-content/uploads/2018/...  
2  https://veganuary.com/wp-content/uploads/2016/...  
3                                                NaN  
4                                                NaN

In [159]:
def clean_df(text):
    # remove HTML
    soup = BeautifulSoup(text, 'lxml')
    text = soup.get_text()

    # Replace Emoticon/Emoji with Text
    text = emoji.demojize(text)
    text = emoticon_fix.emoticon_fix(text)

    # Decoding of abbreviations

    # remove mentions
    text = re.sub("@[A-Za-z0-9]+","", text)
    # remove hashtags
    text = re.sub("#[A-Za-z0-9_]+","", text)
    # remove links
    text = re.sub('https:\/\/\S+', '', text)
    # remove punctuation
    text = re.sub('[%s]' % re.escape(string.punctuation), ' ', text)
    # remove next line
    text = re.sub(r'[^ \w\.]', '', text)
    # remove words containing numbers
    text = re.sub('\w*\d\w*', '', text)
    # remove number
    text = re.sub(r"\d+", "", text)
    # white spaces
    text = text.strip()

    # Replace special characters
    text = re.sub(r'½', '', text)
    # Replace special characters
    text = re.sub(r'½', '', text)
    # Replace double spaces with a single space
    text = re.sub(r'\s+', ' ', text)

    # Convert to lowercase
    text = text.lower()

    # Remove the word 'ingredients'
    text = re.sub('ingredients', '', text)
    text = re.sub('instruction', '', text)

    # Remove specified words
    words_to_remove = ['unit','tsp', 'tbsp', 'veg', 'tablespoon', 'teaspoon', 'add', 'cup', 'minute', 'ingredient', 'teaspoon', 'tablespoon', 'maybe', 'never', 'machine', 'plastic', 'four', 'breakfast', 'always','glass', 'chop', 'cooking', 'time', 'oven', 'lightly', 'medium', 'heat', 'choose', 'recipe',
                    'pre', 'heat', 'preheat', 'packaging', 'peeler', 'might','glass', 'enjoy', 'ideally', 'serving', 'result', 'preferably','night', 'icing', 'semisweet', 'state', 'nibs', 'scale', 'degree', 'pan','speed','meatless','farm','chopped','mix', 'wet', 'link','sometimes','rather','could','table','much','immediately','warm','simply','really','pure','glutenfree','allspice','half' ,'place' ,'drizzle','roast', 'spread','deep', 'cook','just','less','variety','variation','etc','lastly','tblsp','pref']
    for word in words_to_remove:
        text = re.sub(r'\b(?:' + re.escape(word) + r's?)\b', '', text, flags=re.IGNORECASE)


    return text

In [160]:
# df["title"] = df["title"].apply(clean_df).str.lower()
df["ingredients"] = df["ingredients"].apply(clean_df)
df["preparation"] = df["preparation"].apply(clean_df)
df.head(10)


title  \
0                       Rainbow Rice   
1                             Nachos   
2              Baked Apple Charlotte   
3        Choc and Raspberry Porridge   
4           Nākd Mini Bakewell Tarts   
5      Non-Dairy Garlic Herb Gournay   
6               Mexican Bean Lasagne   
7  Butternut Squash and Sage Lasagne   
8                     Shepherd’s Pie   
9             The Best Vegan Burgers   

                                         ingredients  \
0   carrot ribbons  use a  for  frozen peas red c...   
1     co mince or similar can of refried beans ca...   
2    rapeseed oil pitted dates bracupsey apples t...   
3   porridge gluten free rolled oats water of any...   
4   for the shortcrust pastry plain  flour dairyf...   
5   block oz extrafirm waterpacked tofu not silke...   
6    oil onion  green pepper deseeded and  g tinn...   
7   for the butternut pasta butternut squash  oli...   
8   potatoes peeled  onions large carrots button ...   
9   for the patties can black beans rinsed and dr...   

                                         preparation calories  carb protein  \
0   the rice as instructed on the  while the rice...      450    64      10   
1    the  to  the oil in a large   on    the   mi...      483    42      20   
2   you will need an square baking tin for this  ...      415    51       3   
3   the gluten free oats water and your chosen ve...      157    26       5   
4      plus  chilling     the  to and  grease a m...      137    18     2,6   
5   homemade almond or cashew milk is ideal becau...      120     2       2   
6    to c c fan gas mark  oil in a  and fry onion...    174,7  43,9    15,9   
7   the  to c f gas mark to prepare the butternut...      288    31      15   
8   soak your lentils in advance hours before   s...    346,5    26      17   
9     to bake saute garlic onion herbs and spices...      298    42      17   

    fat        types category  is_diary  \
0    19  main course   dinner         0   
1    27       snacks   dinner         1   
2    22  main course   dinner         1   
3     5  main course   dinner         1   
4   5,9  main course   dinner         0   
5    11  main course   dinner         1   
6  19,4  main course   dinner         1   
7    12  main course   dinner         1   
8    20      dessert   dinner         1   
9     7  main course   dinner         0   

                                            img_link  
0  https://veganuary.com/wp-content/uploads/2016/...  
1  https://veganuary.com/wp-content/uploads/2018/...  
2  https://veganuary.com/wp-content/uploads/2016/...  
3                                                NaN  
4                                                NaN  
5                                                NaN  
6                                                NaN  
7                                                NaN  
8                                                NaN  
9                                                NaN

In [161]:
df.to_csv('data_clean.csv', index=False)

# NLTK PREPROCESSING

In [62]:
def get_wordnet_pos(tag):
    # Map POS tag to first character lemmatize() accepts
    tag_dict = {'N': 'n', 'V': 'v', 'R': 'r', 'J': 'a'}
    return tag_dict.get(tag[0], 'n')  # Default to noun if not found

In [63]:
def preprocess_nltk(text_entry):
    # Initialize the NLTK objects for lemmatization
    lemmatizer = WordNetLemmatizer()

    # Define a list of additional custom stopwords
    custom_stopwords = set(['unit','tsp', 'tbsp', 'veg', 'tablespoon', 'teaspoon', 'add', 'cup', 'minute', 'ingredient', 'teaspoon', 'tablespoon', 'maybe', 'never', 'machine', 'plastic', 'four', 'breakfast', 'always','glass', 'chop', 'cooking', 'time', 'oven', 'lightly', 'medium', 'heat', 'choose', 'recipe',
                    'pre', 'heat', 'preheat', 'packaging', 'peeler', 'might','glass', 'enjoy', 'ideally', 'serving', 'result', 'preferably','night', 'icing', 'semisweet', 'state', 'nibs', 'scale', 'degree', 'pan','speed','meatless','farm','chopped','mix', 'wet', 'link','sometimes','rather','could','table','much','immediately','warm','simply','really','pure','glutenfree','allspice','half' ,'place' ,'drizzle','roast', 'spread','deep', 'cook','just','less','variety','variation','etc','lastly','tblsp','pref'])

    # # Combine NLTK stopwords with custom stopwords
    stop_words = set(stopwords.words('english')) | custom_stopwords

    # Tokenize the text and perform part-of-speech tagging
    words = word_tokenize(text_entry)
    pos_tags = pos_tag(words)

    # Apply NER to identify named entities
    named_entities = extract_named_entities(pos_tags)

    # Apply lemmatization to each word, excluding adjectives, proper nouns, verbs, and specific stopwords
    # Apply NER to identify named entities
    named_entities = extract_named_entities(pos_tags)

    # Apply lemmatization to each word, excluding named entities, adjectives, proper nouns, verbs, and specific stopwords
    lemmatized_words = []
    for word, tag in pos_tags:
        # Exclude named entities, adjectives, proper nouns, verbs, and specific stopwords
        if (word, tag) not in named_entities \
                and tag not in ('JJ', 'JJR', 'JJS', 'NNP', 'NNPS', 'VB', 'VBD', 'VBG', 'VBN', 'VBP', 'VBZ') \
                and word.lower() not in stop_words and len(word) > 2:
            # Additional check to exclude words with digits or special characters
            if word.isalpha():
                lemmatized_words.append(lemmatizer.lemmatize(word, pos=get_wordnet_pos(tag)))


    # Join the words back into a single string
    preprocessed_text = ' '.join(lemmatized_words)

    return preprocessed_text

def extract_named_entities(pos_tags):
    chunked_text = ne_chunk(pos_tags)
    named_entities = []
    for subtree in chunked_text:
        if isinstance(subtree, Tree):
            entity = " ".join([word for word, tag in subtree.leaves()])
            named_entities.append((entity, subtree.label()))
    return named_entities

def get_wordnet_pos(tag):
    # Map POS tag to first character lemmatize() accepts
    tag_dict = {'N': 'n', 'V': 'v', 'R': 'r', 'J': 'a'}
    return tag_dict.get(tag[0], 'n')  # Default to noun if not found

In [64]:
df["ingredients"] = df["ingredients"].apply(preprocess_nltk)
df["preparation"] = df["preparation"].apply(preprocess_nltk)
df.head(10)

title  \
0                       Rainbow Rice   
1                             Nachos   
2              Baked Apple Charlotte   
3        Choc and Raspberry Porridge   
4           Nākd Mini Bakewell Tarts   
5      Non-Dairy Garlic Herb Gournay   
6               Mexican Bean Lasagne   
7  Butternut Squash and Sage Lasagne   
8                     Shepherd’s Pie   
9             The Best Vegan Burgers   

                                         ingredients  \
0  carrot ribbon pea cabbage pepper onion miso pa...   
1  mince bean tomato bell pepper bell pepper onio...   
2  oil date apple thats bracupseys dairy milk alm...   
3  porridge gluten water milk pinch salt cacao bu...   
4  pastry dairyfree soya nectar maple water filli...   
5  block extrafirm tofu tofu organic oil lemon ju...   
6  oil onion pepper bean spicy tomato sauce tomat...   
7  butternut pasta butternut squash oil maple syr...   
8  potato onion carrot button mushroom stalk cele...   
9  patty bean beetroot garlic salt pepper coriand...   

                                         preparation calories  carb protein  \
0  rice rice vegetable like ribbon julienne textu...      450    64      10   
1  oil mince bean tomato tomato bell pepper onion...      483    42      20   
2  baking tin line baking tin paper date piece ap...      415    51       3   
3  oat water chosen milk cacao butter drop pinch ...      157    26       5   
4  plus mini muffin tin pastry flour bowl food pr...      137    18     2,6   
5  almond cashew milk consistency ability underta...      120     2       2   
6  fan gas mark oil onion pepper fry stir bean to...    174,7  43,9    15,9   
7  gas mark butternut begin knife way slice end a...      288    31      15   
8  lentil advance hour lentil water hour lot wash...    346,5    26      17   
9  onion herb spice coconut oil onion becomes sti...      298    42      17   

    fat        types category  is_diary  \
0    19  main course   dinner         0   
1    27       snacks   dinner         1   
2    22  main course   dinner         1   
3     5  main course   dinner         1   
4   5,9  main course   dinner         0   
5    11  main course   dinner         1   
6  19,4  main course   dinner         1   
7    12  main course   dinner         1   
8    20      dessert   dinner         1   
9     7  main course   dinner         0   

                                            img_link  
0  https://veganuary.com/wp-content/uploads/2016/...  
1  https://veganuary.com/wp-content/uploads/2018/...  
2  https://veganuary.com/wp-content/uploads/2016/...  
3                                                NaN  
4                                                NaN  
5                                                NaN  
6                                                NaN  
7                                                NaN  
8                                                NaN  
9                                                NaN

In [65]:
df_clean = df.copy()

In [66]:
df_clean

title  \
0                                          Rainbow Rice   
1                                                Nachos   
2                                 Baked Apple Charlotte   
3                           Choc and Raspberry Porridge   
4                              Nākd Mini Bakewell Tarts   
...                                                 ...   
1106                   WEST AFRICAN PEANUT STEW (VEGAN)   
1107                              Almond Flour Crackers   
1108              BAKED VEGAN MAC & CHEESE (+ STOVETOP)   
1109  Southwest Chickpea Salad + Creamy Avocado-Lime...   
1110                     BESY VEGAN MUSHROOM STROGANOFF   

                                            ingredients  \
0     carrot ribbon pea cabbage pepper onion miso pa...   
1     mince bean tomato bell pepper bell pepper onio...   
2     oil date apple thats bracupseys dairy milk alm...   
3     porridge gluten water milk pinch salt cacao bu...   
4     pastry dairyfree soya nectar maple water filli...   
...                                                 ...   
1106  oil water water saute onion clove ginger groun...   
1107  flaxseed meal water flour almond meal addins h...   
1108  package pasta choice work package optional two...   
1109  romaine lettuce chickpea grape cherry tomato c...   
1110  butter miyokos onion shallot finely clove mush...   

                                            preparation calories   carb  \
0     rice rice vegetable like ribbon julienne textu...      450     64   
1     oil mince bean tomato tomato bell pepper onion...      483     42   
2     baking tin line baking tin paper date piece ap...      415     51   
3     oat water chosen milk cacao butter drop pinch ...      157     26   
4     plus mini muffin tin pastry flour bowl food pr...      137     18   
...                                                 ...      ...    ...   
1106  saute pot oil water onion ginger chili pepper ...      276   22,3   
1107  line sheet paper flax mixture bowl flaxseed me...       87    2,5   
1108  pot water boil noodle aside crumb water start ...      436   55,6   
1109  diy tortilla strip toaster corn tortilla oil s...    252,5  26,95   
1110  pasta noodle package direction dente drain res...      447   66,7   

     protein    fat        types category  is_diary  \
0         10     19  main course   dinner         0   
1         20     27       snacks   dinner         1   
2          3     22  main course   dinner         1   
3          5      5  main course   dinner         1   
4        2,6    5,9  main course   dinner         0   
...      ...    ...          ...      ...       ...   
1106      15   17,7  main course   dinner         1   
1107     2,4    2,5  main course   dinner         0   
1108    14,4   18,3  main course   dinner         1   
1109    9,45  14,35  main course    lunch         0   
1110    15,2     14  main course   dinner         1   

                                               img_link  
0     https://veganuary.com/wp-content/uploads/2016/...  
1     https://veganuary.com/wp-content/uploads/2018/...  
2     https://veganuary.com/wp-content/uploads/2016/...  
3                                                   NaN  
4                                                   NaN  
...                                                 ...  
1106                                                NaN  
1107                                                NaN  
1108                                                NaN  
1109                                                NaN  
1110                                                NaN  

[1111 rows x 11 columns]

# BUILDING WORD2VEC

In [67]:
import pickle

In [163]:
model_filename = "word2vec_model.bin"
tokens_filename = "tokens.pkl"
df_clean_filename = "data_clean.csv"

In [164]:
df_clean = pd.read_csv(df_clean_filename)

In [165]:
def tokenize_text(text_list):
    all_tokens = []
    for text in text_list:
        all_tokens.append(word_tokenize(text))
    return all_tokens

def save_tokens(tokens, filename):
    with open(filename, 'wb') as file:
        pickle.dump(tokens, file)

def tokenize_and_save(tokens_filename):
    all_text = df_clean['title'] + ' ' + df_clean['ingredients'] + ' ' + df_clean['preparation']
    all_tokens = tokenize_text(all_text)
    save_tokens(all_tokens, tokens_filename)

    return all_tokens

tokenize_and_save(tokens_filename)

[['Rainbow',
  'Rice',
  'carrot',
  'ribbons',
  'use',
  'a',
  'for',
  'frozen',
  'peas',
  'red',
  'cabbage',
  'yellow',
  'peppers',
  'red',
  'onion',
  'miso',
  'paste',
  'of',
  'chinese',
  'five',
  'spice',
  'of',
  'soy',
  'sauce',
  'of',
  'oil',
  'white',
  'rice',
  'the',
  'rice',
  'as',
  'instructed',
  'on',
  'the',
  'while',
  'the',
  'rice',
  'prep',
  'the',
  'vegetables',
  'i',
  'like',
  'a',
  'of',
  'diced',
  'ribbon',
  'julienne',
  'to',
  'create',
  'a',
  'of',
  'textures',
  'when',
  'the',
  'is',
  'ready',
  'the',
  'oil',
  'to',
  'a',
  'frying',
  'or',
  'wok',
  'and',
  'let',
  'it',
  'get',
  'hot',
  'before',
  'throwing',
  'in',
  'the',
  'carrots',
  'and',
  'cabbage',
  'take',
  'a',
  'little',
  'longer',
  'to',
  'so',
  'i',
  'put',
  'them',
  'in',
  'first',
  'and',
  'then',
  'the',
  'rest',
  'of',
  'the',
  'goes',
  'in',
  'a',
  'couple',
  'of',
  'later',
  'keep',
  'giving',
  'the',


In [166]:
def load_tokens(tokens_filename):
    with open(tokens_filename, 'rb') as file:
        return pickle.load(file)

In [167]:
def save_word2vec_model(model, filename):
    model.save(filename)

def train_word2vec_model(sentences, vector_size=100, window=5, min_count=1, workers=4):
    return Word2Vec(sentences=sentences, vector_size=vector_size, window=window, min_count=min_count, workers=workers)

def train_and_save_model(tokens_filename):
    all_tokens = load_tokens(tokens_filename)

    w2v_model = train_word2vec_model(all_tokens)
    save_word2vec_model(w2v_model, model_filename)

    return w2v_model

train_and_save_model(tokens_filename)

In [168]:
def load_word2vec_model(filename):
    return gensim.models.Word2Vec.load(filename)

In [169]:
def generate_user_input_vector(model, user_input):
    user_input_tokens = word_tokenize(user_input)
    user_input_vector = [0] * model.vector_size
    num_tokens = 0

    for token in user_input_tokens:
        if token in model.wv:
            user_input_vector = [a + b for a, b in zip(user_input_vector, model.wv[token])]
            num_tokens += 1

    if num_tokens > 0:
        user_input_vector = [x / num_tokens for x in user_input_vector]

    return np.array(user_input_vector).reshape(1, -1)

In [170]:
def calculate_recipe_vectors(model, recipes_tokens):
    all_recipes_vector = []
    for recipe_tokens in recipes_tokens:
        recipe_vector = [0] * model.vector_size
        num_tokens = 0

        for token in recipe_tokens:
            if token in model.wv:
                recipe_vector = [a + b for a, b in zip(recipe_vector, model.wv[token])]
                num_tokens += 1

        if num_tokens > 0:
            recipe_vector = [x / num_tokens for x in recipe_vector]

        all_recipes_vector.append(recipe_vector)

    return np.array(all_recipes_vector)

In [171]:
def recommend_top_recipes(user_input_vector, all_recipes_vector, data, N=20):
    similarities = cosine_similarity(user_input_vector, all_recipes_vector)
    top_indices = similarities.argsort()[0][-N:][::-1]
    top_recipes_titles = [data['title'][idx] for idx in top_indices]
    return top_recipes_titles

In [190]:
import json

def main():
    all_tokens = load_tokens(tokens_filename)
    w2v_model = load_word2vec_model(model_filename)

    user_input = input("Enter your ingredients (e.g., cheese, chocolate): ")
    user_input_vector = generate_user_input_vector(w2v_model, user_input)

    all_recipes_vector = calculate_recipe_vectors(w2v_model, all_tokens)

    top_recipes_titles = recommend_top_recipes(user_input_vector, all_recipes_vector, data)

    result_df = data[data['title'].isin(top_recipes_titles)].reset_index(drop=True)

    # Create a list to store the results
    results_list = []

    # Reset the index before iterating
    result_df = result_df.reset_index(drop=True)

    for _, row in result_df.iterrows():
        result = {
            "title": row["title"],
            "ingredients": row["ingredients"],
            "preparation": row["preparation"],
            "calories": row["calories"],
            "carb": row["carb"],
            "protein": row["protein"],
            "fat": row["fat"],
            "types": row["types"],
            "category": row["category"],
            "isdairy": row["is_diary"],

        }
        results_list.append(result)

    # Convert the results to JSON
    json_result = json.dumps(results_list, indent=2)

    # Print or save the JSON result
    print(json_result)

    return results_list

# Call the main function
json_result = main()


Enter your ingredients (e.g., cheese, chocolate): chocolate, banana
[
  {
    "title": "Marbled Chocolate Banana Bread",
    "ingredients": "\nIngredients :\n\n250 g plain flour\n65 g coconut sugar\u00a0\n13 cup coconut oil melted see notes\n3 tbsp nondairy milk I used oat milk\n12 tsp apple cider vinegar\n3 very ripe bananas\n1 tsp baking powder\n12 tsp baking soda\n14 tsp  pink salt\n12 tsp vanilla extract\n\n\nChocolate batter\n40 g cacao powder\n30 g coconut sugar\n3 tbsp nondairy milk\n1 tbsp coconut oil\n\n",
    "preparation": "Pre-heat oven to 180\u00b0C/ 160\u00b0C fan and line a loaf tin with parchment paper.\nTo make the butter milk mix oat milk with apple cider vinegar and set aside for 5-10 minutes.\nMix plain flour, baking soda, baking powder and pink salt.\nIn another bowl mash 3 bananas, then mix in your coconut sugar.\nSlowly mix in buttermilk and coconut oil with the mashed banana mixture.\nCombine wet and dry and ingredients.\nDivide the batter in half.\nAdd in cacao

# TEST WORD2VEC

In [173]:
# Load the saved Word2Vec model
model_filename = "word2vec_model.bin"  # Replace with your actual filename
w2v_model = Word2Vec.load(model_filename)

In [174]:
# Evaluate on an analogy task
def analogy_test(model, word1, word2, word3):
    try:
        predicted_word = model.wv.most_similar(positive=[word2, word3], negative=[word1])[0][0]
        return predicted_word
    except KeyError:
        return "One or more words not in the model's vocabulary."

# Test the analogy function
print(analogy_test(w2v_model, 'vanilla', 'chocolate', 'milk'))



# For a more thorough evaluation, you would run these tests on a standard dataset of analogies and similarities.

cream


In [183]:
# Evaluate on a similarity task
def similarity_test(model, word1, word2):
    try:
        similarity = model.wv.similarity(word1, word2)
        return similarity
    except KeyError:
        return "One or more words not in the model's vocabulary."

# Test the similarity function
print(similarity_test(w2v_model, 'yogurt', 'dairy'))  # Outputs a similarity score

0.92963004
